In [ ]:
# we will study the hyperparamter tuning of fully connected scatternet

# first find optimal number of layers and neuron numbers
# second optimize the batch size and number of epochs for the best learned architecture


### Loading the dataset here

In [1]:
import numpy as np

import h5py
from sklearn.model_selection import train_test_split

#now load this dataset 
h5f = h5py.File('./datasets/s8_sio2tio2.h5','r')
X = h5f['sizes'][:]
Y = h5f['spectrum'][:]

#get the ranges of the loaded data
num_layers = X.shape[1]
num_lpoints = Y.shape[1]
size_max = np.amax(X)
size_min = np.amin(X)
size_av = 0.5*(size_max + size_min)

#this information is not given in the dataset
lam_min = 300
lam_max = 1200
lams = np.linspace(lam_min, lam_max, num_lpoints)

#create a train - test split of the dataset
x_train, x_test, y_train, y_test = train_test_split(X, Y, test_size=0.4, random_state=42)

# normalize inputs 
x_train = (x_train - 50)/20 
x_test = (x_test - 50)/20 

print("Dataset has been loaded")
print("x-train", x_train.shape)
print("x-test ", x_test.shape)
print("y-train", y_train.shape)
print("y-test ", y_test.shape)

/home/hegder/anaconda3/envs/deep/lib/python3.6/importlib/_bootstrap.py:219: RuntimeWarning: numpy.dtype size changed, may indicate binary incompatibility. Expected 96, got 88
  return f(*args, **kwds)
/home/hegder/anaconda3/envs/deep/lib/python3.6/importlib/_bootstrap.py:219: RuntimeWarning: numpy.dtype size changed, may indicate binary incompatibility. Expected 96, got 88
  return f(*args, **kwds)
/home/hegder/anaconda3/envs/deep/lib/python3.6/importlib/_bootstrap.py:219: RuntimeWarning: numpy.dtype size changed, may indicate binary incompatibility. Expected 96, got 88
  return f(*args, **kwds)


Dataset has been loaded
x-train (60000, 8)
x-test  (40000, 8)
y-train (60000, 250)
y-test  (40000, 250)


### create models here

In [2]:
import scnets as scn
from IPython.display import SVG
from keras.utils.vis_utils import model_to_dot

#define and visualize the model here
model = scn.fullycon(num_layers, num_lpoints, 4, 500, 2)
model.summary()
#SVG(model_to_dot(model).create(prog='dot', format='svg'))


Using MXNet backend


_________________________________________________________________
Layer (type)                 Output Shape              Param #   
first (Dense)                (None, 250)               2250      
_________________________________________________________________
H0 (Dense)                   (None, 250)               62750     
_________________________________________________________________
H1 (Dense)                   (None, 250)               62750     
_________________________________________________________________
H2 (Dense)                   (None, 250)               62750     
_________________________________________________________________
H3 (Dense)                   (None, 250)               62750     
_________________________________________________________________
last (Dense)                 (None, 250)               62750     
Total params: 316,000
Trainable params: 316,000
Non-trainable params: 0
_________________________________________________________________


In [ ]:
x_t, x_v, y_t, y_v = train_test_split(x_train, y_train, test_size=0.2, random_state=42)
history = model.fit(x_t, y_t,
                    batch_size=64,
                    epochs=500, 
                    verbose=1,
                    validation_data=(x_v, y_v))


In [ ]:
from sklearn.model_selection import GridSearchCV
from keras.models import Sequential
from keras.layers import Dense
from keras.wrappers.scikit_learn import KerasClassifier

model = KerasClassifier(build_fn=scn.fullycon, in_size=8, out_size=250, N_gpus=1, epochs=500, verbose=1)

param_grid = dict(N_hidden=[1,2,3,4,5], N_neurons=[250, 500, 1000])
grid = GridSearchCV(estimator=model, param_grid=param_grid, n_jobs=1, verbose=1)
grid_result = grid.fit(x_train, y_train)




Fitting 3 folds for each of 15 candidates, totalling 45 fits
Epoch 1/500
 3424/40000 [=>............................] - ETA: 2s - loss: 2767.1082 - acc: 0.0213  

/home/hegder/anaconda3/envs/deep/lib/python3.6/site-packages/mxnet/module/bucketing_module.py:408: UserWarning: Optimizer created manually outside Module but rescale_grad is not normalized to 1.0/batch_size/num_workers (1.0 vs. 0.03125). Is this intended?
  force_init=force_init)


40000/40000 [==============================] - 2s 43us/step - loss: 583.2747 - acc: 0.1176
Epoch 2/500
40000/40000 [==============================] - 2s 44us/step - loss: 210.3483 - acc: 0.2964
Epoch 3/500
40000/40000 [==============================] - 2s 45us/step - loss: 178.0033 - acc: 0.4047
Epoch 4/500
40000/40000 [==============================] - 2s 43us/step - loss: 160.5207 - acc: 0.4632
Epoch 5/500
40000/40000 [==============================] - 2s 46us/step - loss: 151.2789 - acc: 0.4940
Epoch 6/500
40000/40000 [==============================] - 2s 43us/step - loss: 143.0541 - acc: 0.5121
Epoch 7/500
40000/40000 [==============================] - 2s 45us/step - loss: 135.8894 - acc: 0.5229
Epoch 8/500
40000/40000 [==============================] - 2s 46us/step - loss: 129.3540 - acc: 0.5414
Epoch 9/500
40000/40000 [==============================] - 2s 50us/step - loss: 123.8888 - acc: 0.5578
Epoch 10/500
40000/40000 [==============================] - 2s 46us/step - loss: 122.

40000/40000 [==============================] - 2s 46us/step - loss: 48.0683 - acc: 0.8099
Epoch 81/500
40000/40000 [==============================] - 2s 45us/step - loss: 48.3724 - acc: 0.8119
Epoch 82/500
40000/40000 [==============================] - 2s 44us/step - loss: 47.7136 - acc: 0.8132
Epoch 83/500
40000/40000 [==============================] - 2s 43us/step - loss: 47.6136 - acc: 0.8118
Epoch 84/500
40000/40000 [==============================] - 2s 43us/step - loss: 46.4129 - acc: 0.8121
Epoch 85/500
40000/40000 [==============================] - 2s 42us/step - loss: 47.1255 - acc: 0.8135
Epoch 86/500
40000/40000 [==============================] - 2s 43us/step - loss: 46.6991 - acc: 0.8107
Epoch 87/500
40000/40000 [==============================] - 2s 43us/step - loss: 46.4053 - acc: 0.8158
Epoch 88/500
40000/40000 [==============================] - 2s 43us/step - loss: 46.8279 - acc: 0.8167
Epoch 89/500
40000/40000 [==============================] - 2s 44us/step - loss: 46.16

40000/40000 [==============================] - 2s 44us/step - loss: 39.4876 - acc: 0.8411
Epoch 160/500
40000/40000 [==============================] - 2s 43us/step - loss: 39.2777 - acc: 0.8398
Epoch 161/500
40000/40000 [==============================] - 2s 43us/step - loss: 39.6109 - acc: 0.8372
Epoch 162/500
40000/40000 [==============================] - 2s 43us/step - loss: 39.0171 - acc: 0.8372
Epoch 163/500
40000/40000 [==============================] - 2s 42us/step - loss: 38.9856 - acc: 0.8378
Epoch 164/500
40000/40000 [==============================] - 2s 45us/step - loss: 39.1003 - acc: 0.8415
Epoch 165/500
40000/40000 [==============================] - 2s 43us/step - loss: 38.9179 - acc: 0.8396
Epoch 166/500
40000/40000 [==============================] - 2s 43us/step - loss: 38.9712 - acc: 0.8431
Epoch 167/500
40000/40000 [==============================] - 2s 44us/step - loss: 38.5523 - acc: 0.8392
Epoch 168/500
40000/40000 [==============================] - 2s 45us/step - lo

...

40000/40000 [==============================] - 2s 44us/step - loss: 34.4638 - acc: 0.8531
Epoch 316/500
40000/40000 [==============================] - 2s 45us/step - loss: 34.3475 - acc: 0.8531
Epoch 317/500
40000/40000 [==============================] - 2s 47us/step - loss: 34.5912 - acc: 0.8515
Epoch 318/500
40000/40000 [==============================] - 2s 42us/step - loss: 34.3538 - acc: 0.8533
Epoch 319/500
40000/40000 [==============================] - 2s 44us/step - loss: 34.5053 - acc: 0.8548
Epoch 320/500
40000/40000 [==============================] - 2s 43us/step - loss: 34.5437 - acc: 0.8518
Epoch 321/500
40000/40000 [==============================] - 2s 46us/step - loss: 34.3846 - acc: 0.8531
Epoch 322/500
40000/40000 [==============================] - 2s 45us/step - loss: 34.4208 - acc: 0.8564
Epoch 323/500
40000/40000 [==============================] - 2s 48us/step - loss: 34.5484 - acc: 0.8506
Epoch 324/500
40000/40000 [==============================] - 2s 46us/step - lo

40000/40000 [==============================] - 2s 43us/step - loss: 33.3614 - acc: 0.8596
Epoch 394/500
40000/40000 [==============================] - 2s 45us/step - loss: 33.3544 - acc: 0.8582
Epoch 395/500
40000/40000 [==============================] - 2s 45us/step - loss: 33.4453 - acc: 0.8562
Epoch 396/500
40000/40000 [==============================] - 2s 45us/step - loss: 33.2711 - acc: 0.8571
Epoch 397/500
40000/40000 [==============================] - 2s 44us/step - loss: 33.0012 - acc: 0.8565
Epoch 398/500
40000/40000 [==============================] - 2s 43us/step - loss: 33.1989 - acc: 0.8578
Epoch 399/500
40000/40000 [==============================] - 2s 44us/step - loss: 33.1854 - acc: 0.8599
Epoch 400/500
40000/40000 [==============================] - 2s 42us/step - loss: 33.1324 - acc: 0.8582
Epoch 401/500
40000/40000 [==============================] - 2s 43us/step - loss: 33.1862 - acc: 0.8601
Epoch 402/500
40000/40000 [==============================] - 2s 43us/step - lo

40000/40000 [==============================] - 2s 43us/step - loss: 32.2166 - acc: 0.8615
Epoch 472/500
40000/40000 [==============================] - 2s 48us/step - loss: 32.3152 - acc: 0.8622
Epoch 473/500
40000/40000 [==============================] - 2s 44us/step - loss: 32.5202 - acc: 0.8634
Epoch 474/500
40000/40000 [==============================] - 2s 46us/step - loss: 32.3509 - acc: 0.8608
Epoch 475/500
40000/40000 [==============================] - 2s 49us/step - loss: 32.2972 - acc: 0.8631
Epoch 476/500
40000/40000 [==============================] - 2s 49us/step - loss: 32.2340 - acc: 0.8604
Epoch 477/500
40000/40000 [==============================] - 2s 47us/step - loss: 32.4099 - acc: 0.8590
Epoch 478/500
40000/40000 [==============================] - 2s 46us/step - loss: 32.2556 - acc: 0.8640
Epoch 479/500
40000/40000 [==============================] - 2s 49us/step - loss: 32.2823 - acc: 0.8599
Epoch 480/500
40000/40000 [==============================] - 2s 42us/step - lo

/home/hegder/anaconda3/envs/deep/lib/python3.6/site-packages/mxnet/module/bucketing_module.py:408: UserWarning: Optimizer created manually outside Module but rescale_grad is not normalized to 1.0/batch_size/num_workers (1.0 vs. 0.03125). Is this intended?
  force_init=force_init)


40000/40000 [==============================] - 2s 43us/step - loss: 590.7578 - acc: 0.1155
Epoch 2/500
40000/40000 [==============================] - 2s 45us/step - loss: 213.6523 - acc: 0.2773
Epoch 3/500
40000/40000 [==============================] - 2s 45us/step - loss: 182.5214 - acc: 0.3849
Epoch 4/500
40000/40000 [==============================] - 2s 46us/step - loss: 165.6190 - acc: 0.4341
Epoch 5/500
40000/40000 [==============================] - 2s 44us/step - loss: 154.0008 - acc: 0.4641
Epoch 6/500
40000/40000 [==============================] - 2s 43us/step - loss: 146.4385 - acc: 0.4901
Epoch 7/500
40000/40000 [==============================] - 2s 44us/step - loss: 138.4695 - acc: 0.5204
Epoch 8/500
40000/40000 [==============================] - 2s 43us/step - loss: 130.9537 - acc: 0.5291
Epoch 9/500
40000/40000 [==============================] - 2s 43us/step - loss: 128.4725 - acc: 0.5379
Epoch 10/500
40000/40000 [==============================] - 2s 44us/step - loss: 122.

In [ ]:
grid_result

In [ ]:
grid_result.best_params_